## Лабораторная работа 2. Продвинутое использование LLM

### 1. Квантизация

Используем более крупную модель, которая может не поместиться в нашу видеопамять. Для тех, кто работает в датасфере с видеопамятью 16гб это не должно стать проблемой, но те, кто работают с домашних компьютеров могут столкнуться с ошибкой памяти CUDA. Однако, попробуем воспользоваться квантизацией, то есть использованием меньшего количества бит для каждого параметра.

In [ ]:
%pip install -U bitsandbytes

In [ ]:
%pip install pandas

In [ ]:
%pip install scikit-learn

### 1.1 Квантизация

In [ ]:
import torch
from transformers import AutoModelForCausalLM, AutoTokenizer, BitsAndBytesConfig
device = "cuda"

quantization_config = BitsAndBytesConfig(load_in_4bit=True)

model = AutoModelForCausalLM.from_pretrained(
    "Qwen/Qwen2-7B-Instruct",
    device_map=device,
    torch_dtype=torch.bfloat16,
    quantization_config=quantization_config
)
tokenizer = AutoTokenizer.from_pretrained("Qwen/Qwen2-7B-Instruct")

Какой числовой тип использует модель `Qwen2` для своих весов по умолчанию? Почему?

Ответ: ...

Как, зная количество параметров модели, примерно высчитать, сколько модель будет занимать в оперативной памяти компьютера при использовании различных числовых типов данных? Какова цена использования более маленьких типов (`int8`, `int4`)?

Ответ: ...

### 1.2 Сравнение работы моделей

Сравните работу модели `Qwen/Qwen2-7B-Instruct` в `int4` квантизации и `Qwen/Qwen2-1.5B-Instruct` в `bfloat16`. Оцените качество и скорость ответов.

Подсказка. Для замера времени ответа используйте встроенную библиотеку `time`

### 2. Использование рассуждений (reasoning) во взаимодействии с LLM

Загрузите данные из `algebra__linear_1d_test.csv` в датафрейм. Это датасет простых алгебраических задач, которые новая модель `Qwen2` должна иметь возможность решать

Для удобства валидации ответов конвертируем строковые ответы в `float`

In [ ]:
def convert_to_float(frac_str):
    try:
        return float(frac_str)
    except ValueError:
        num, denom = frac_str.split('/')
        try:
            leading, num = num.split(' ')
            whole = float(leading)
        except ValueError:
            whole = 0
        frac = float(num) / float(denom)
        return whole - frac if whole < 0 else whole + frac

In [ ]:
import pandas as pd

df = pd.read_csv("./algebra__linear_1d_test.csv")
df = df.sample(50)  # выберем случайные 50 задач
df.answer = df.answer.apply(lambda x: convert_to_float(x[2:-3]))  # представим данные в удобном для нас виде
df.question = df.question.apply(lambda x: x[2:-3])
df

Как и в прошлой работе, загрузите модель в память. Используйте полученные в прошлой лабораторной функции

Примечание. Те, у кого не хватает GPU памяти для использования `Qwen/Qwen2-Math-7B-Instruct` могут воспользоваться квантизацией или моделью `Qwen/Qwen2-Math-1.5B-Instruct`

In [ ]:
import torch
from transformers import AutoModelForCausalLM, AutoTokenizer
device = "cuda"

model = AutoModelForCausalLM.from_pretrained(
    "Qwen/Qwen2-Math-7B-Instruct",
    device_map=device,
    torch_dtype=torch.bfloat16
)
tokenizer = AutoTokenizer.from_pretrained("Qwen/Qwen2-Math-7B-Instruct")

### 2.1 Решение без рассуждений

Для начала попробуйте попросить модель возвращать только ответ. Используйте промпт `Solve the following mathematical problem. Return only the correct answer, which is a float number and nothing else.\n\nTask:\n\n{text}`.

In [ ]:
import re

def extract_first_number_from_string(text):
    return float(re.findall("[-+]?[.]?[\d]+(?:,\d\d\d)*[\.]?\d*(?:[eE][-+]?\d+)?", text)[-1])

Чтобы оценить качество ответов, вычислите точность (`accuracy`) и `среднюю абсолютную ошибку`. Изучите, что это такое и оцените, насколько хороши были ответы модели в данном случае.

In [ ]:
print("accuracy:", accuracy_metrics(trues, preds))
print("MAE:", mean_absolute_error(trues, preds))

### 2.2 Решение с рассуждениями

Теперь попробуем добавить рассуждения (reasoning) в ответ модели. Используйте теперь, например, промпт `Solve the following mathematical problem, the solve should be a float number. Return full course of reasoning to solve this problem. At the end write your answer in the form 'Answer: your answer'.\n\nTask:\n\n{text}`.

In [ ]:
print("accuracy:", accuracy_metrics(trues, preds))
print("MAE:", mean_absolute_error(trues, preds))